Import Relevant Libraries

In [21]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as SNS

from sklearn.dummy import DummyClassifier
from sklearn.preprocessing import OneHotEncoder, OrdinalEncoder, StandardScaler
from sklearn.linear_model import LogisticRegression
from sklearn.model_selection import cross_val_score, GridSearchCV, train_test_split
from sklearn.tree import DecisionTreeClassifier
from sklearn.ensemble import RandomForestClassifier, AdaBoostClassifier, GradientBoostingClassifier
from sklearn.metrics import accuracy_score, recall_score, precision_score, confusion_matrix, \
                            plot_confusion_matrix, plot_roc_curve, roc_auc_score
from sklearn.pipeline import Pipeline
from sklearn.compose import ColumnTransformer
from sklearn.neighbors import KNeighborsClassifier

import xgboost

In [22]:
# read in cleaned data file
df = pd.read_csv('final_data.csv', index_col=0)
df.head()

amount_tsh  funder  gps_height installer                    basin  \
0      6000.0   Other        1390     Other               Lake Nyasa   
1         0.0   Other        1399     Other            Lake Victoria   
2        25.0   Other         686     Other                  Pangani   
3         0.0  Unicef         263     Other  Ruvuma / Southern Coast   
4         0.0   Other           0     Other            Lake Victoria   

   region_code  district_code public_meeting scheme_management  permit  \
0           11              5           True               VWC   False   
1           20              2        Unknown             Other    True   
2           21              4           True               VWC    True   
3           90             63           True               VWC    True   
4           18              1           True           Unknown    True   

  extraction_type_class management         payment water_quality  \
0               gravity        vwc    pay annually          soft   
1               gravity        wug       never pay          soft   
2               gravity        vwc  pay per bucket          soft   
3           submersible        vwc       never pay          soft   
4               gravity      other       never pay          soft   

       quantity                source              waterpoint_type  \
0        enough                spring           communal standpipe   
1  insufficient  rainwater harvesting           communal standpipe   
2        enough                   dam  communal standpipe multiple   
3           dry           machine dbh  communal standpipe multiple   
4      seasonal  rainwater harvesting           communal standpipe   

     status_group  age  
0      functional   23  
1      functional   12  
2      functional   13  
3  non functional   36  
4      functional   22

In [23]:
# Create our predictors and target
X = df.drop('status_group', axis=1)
y = df.status_group

In [24]:
# Split the data into training and testing sets
X_train, X_test, y_train, y_test = train_test_split(X, y, random_state=42)

In [25]:
X_train.head()

amount_tsh   funder  gps_height installer                    basin  \
4442          0.0    Other         947     Other  Ruvuma / Southern Coast   
11884         0.0    Other         227     Other  Ruvuma / Southern Coast   
38674      4000.0    Other        1980     Other                   Rufiji   
34584       500.0   Unicef        1471       DWE                   Rufiji   
58645         0.0  Unknown           0   Unknown                   Rufiji   

       region_code  district_code public_meeting scheme_management  permit  \
4442            10              2           True               VWC    True   
11884            8              3           True               VWC   False   
38674           11              7           True               VWC    True   
34584           11              4           True               WUA    True   
58645           12              7           True               VWC    True   

      extraction_type_class management       payment water_quality  quantity  \
4442                gravity        vwc     never pay          soft    enough   
11884               gravity        vwc     never pay       unknown       dry   
38674               gravity        vwc  pay annually          soft    enough   
34584               gravity        wua   pay monthly          soft    enough   
58645               gravity        vwc   pay monthly          soft  seasonal   

                     source     waterpoint_type  age  
4442                  river  communal standpipe   35  
11884  rainwater harvesting  communal standpipe   20  
38674                 river  communal standpipe   19  
34584                 river  communal standpipe   44  
58645                 river  communal standpipe   22

In [26]:
# Confirm that out training data set is 3x larger than the testing dataset
print(X_train.shape, X_test.shape)

(44271, 18) (14758, 18)


# Modeling

### Dummy Model

First, we will create a dummy model that always predicts the most frequent class. In this case, our dummy model will predict that all of the water wells are functional.

In [27]:
# Instantiate our dummy regressor object
dummy = DummyClassifier(strategy='most_frequent')

In [28]:
# Fit the model on our training data
dummy.fit(X_train, y_train)

DummyClassifier(strategy='most_frequent')

In [29]:
# Inspect the accuracy of our initial dummy model
dummy.score(X_train, y_train)

0.5457071220437758

Our dummy model accuracy of 54.6% reflects the distribution of our target. Thus, if we always predict that a water well is functional, we will achieve 54.6% accuracy.

### Set Up Column Transformer

In [62]:
# Create our sub pipelines for numeric and categorial data
subpipe_num = Pipeline(steps=[('ss', StandardScaler())])
subpipe_cat = Pipeline(steps=[('ohe', OneHotEncoder(sparse=False,
                                                    handle_unknown='ignore'))])

In [63]:
# Include our sub pipelines in a column transformer to OHE our categorial variables and scale our numerical variables.
CT = ColumnTransformer(transformers=[('subpipe_num', subpipe_num, [0,2,17]), 
                                     ('subpipe_cat', subpipe_cat, [1,3,4,5,6,7,8,9,10,11,12,13,14,15,16])])

### Create Pipeline for Simple Models

In [64]:
logreg_pipe = Pipeline(steps=[('CT', CT), 
                              ('logreg', LogisticRegression(random_state=42))])

knn_pipe = Pipeline(steps=[('CT', CT), 
                              ('knn', KNeighborsClassifier())])

dtc_pipe = Pipeline(steps=[('CT', CT), 
                              ('dtc', DecisionTreeClassifier(random_state=42))])


In [65]:
# Fit each pipeline to our training data
logreg_pipe.fit(X_train, y_train)
knn_pipe.fit(X_train, y_train)
dtc_pipe.fit(X_train, y_train)

/Users/zacharypollatsek/opt/anaconda3/envs/learn-env/lib/python3.8/site-packages/sklearn/linear_model/_logistic.py:762: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#logistic-regression
  n_iter_i = _check_optimize_result(


Pipeline(steps=[('CT',
                 ColumnTransformer(transformers=[('subpipe_num',
                                                  Pipeline(steps=[('ss',
                                                                   StandardScaler())]),
                                                  [0, 2, 17]),
                                                 ('subpipe_cat',
                                                  Pipeline(steps=[('ohe',
                                                                   OneHotEncoder(handle_unknown='ignore',
                                                                                 sparse=False))]),
                                                  [1, 3, 4, 5, 6, 7, 8, 9, 10,
                                                   11, 12, 13, 14, 15, 16])])),
                ('dtc', DecisionTreeClassifier(random_state=42))])

In [66]:
# Get initial accuracy scores for each our our simple classifier models
logreg_score = logreg_pipe.score(X_train, y_train)
knn_score = knn_pipe.score(X_train, y_train)
dtc_score = dtc_pipe.score(X_train, y_train)

In [67]:
# Print out initial accuracy scores
print(f'Logistic Regression Accuracy: {round(logreg_score * 100, 2)}%')
print(f'KNearestNeighbors Accuracy: {round(knn_score * 100, 2)}%')
print(f'DecisionTree Accuracy: {round(dtc_score * 100, 2)}%')

Logistic Regression Accuracy: 74.68%
KNearestNeighbors Accuracy: 82.61%
DecisionTree Accuracy: 94.4%


Our initial numbers appear to be relatively good. We expect our decision tree classifier to be overfit given the high accuracy score. We will dive deeper into more complex models below to maximize our accuracy and recall. 

### Random Forest

In [68]:
# Create our random forest pipeline to incorporate column transformer
rfc_pipe = Pipeline(steps=[('CT', CT),
                          ('rfc', RandomForestClassifier(random_state=42))])

In [69]:
# Fit our random forest classifier to the training data
rfc_pipe.fit(X_train, y_train)

Pipeline(steps=[('CT',
                 ColumnTransformer(transformers=[('subpipe_num',
                                                  Pipeline(steps=[('ss',
                                                                   StandardScaler())]),
                                                  [0, 2, 17]),
                                                 ('subpipe_cat',
                                                  Pipeline(steps=[('ohe',
                                                                   OneHotEncoder(handle_unknown='ignore',
                                                                                 sparse=False))]),
                                                  [1, 3, 4, 5, 6, 7, 8, 9, 10,
                                                   11, 12, 13, 14, 15, 16])])),
                ('rfc', RandomForestClassifier(random_state=42))])

In [70]:
rfc_pipe.score(X_train, y_train)

0.9439813873641888

In [71]:
cross_val_score(estimator=rfc_pipe, X=X_train, y=y_train, cv=5)

array([0.7796725 , 0.78032528, 0.7798735 , 0.78134177, 0.77716286])

Given that our cross validation scores were significantly lower than the accuracy score from our single random forest classifier, we can say that this model is overfit to the training data. We will perform a grid search in order to optimize the hyper parameters of this classifier.

In [72]:
# create our grid for the grid search parameters
params = {'rfc__n_estimators': [50, 100, 150],
          'rfc__min_samples_split': [2, 10, 50],
          'rfc__max_depth': [5, 10, 15]}

# set up GridSearchCV object
grid_rfc = GridSearchCV(rfc_pipe, param_grid=params, cv=5)

In [73]:
# fit our grid object for random forests to the training data
grid_rfc.fit(X_train, y_train)

GridSearchCV(cv=5,
             estimator=Pipeline(steps=[('CT',
                                        ColumnTransformer(transformers=[('subpipe_num',
                                                                         Pipeline(steps=[('ss',
                                                                                          StandardScaler())]),
                                                                         [0, 2,
                                                                          17]),
                                                                        ('subpipe_cat',
                                                                         Pipeline(steps=[('ohe',
                                                                                          OneHotEncoder(handle_unknown='ignore',
                                                                                                        sparse=False))]),
                                            

In [74]:
grid_rfc.best_params_

{'rfc__max_depth': 15, 'rfc__min_samples_split': 2, 'rfc__n_estimators': 100}

In [75]:
grid_rfc.best_score_

0.7832668202933669

**From our initial grid search, we attained an accuracy of 78.3% using a max_depth of 15, a min_samples_split of 2, and an n_estimators of 100.**


In [76]:
pd.DataFrame(grid_rfc.cv_results_)

mean_fit_time  std_fit_time  mean_score_time  std_score_time  \
0        1.478690      0.136425         0.100926        0.009912   
1        2.410543      0.059405         0.124244        0.002386   
2        3.481135      0.030680         0.159058        0.002828   
3        1.302624      0.014334         0.095788        0.004225   
4        2.405131      0.020833         0.125268        0.001190   
5        3.456263      0.017454         0.157260        0.001306   
6        1.312027      0.013437         0.092828        0.001090   
7        2.420723      0.060456         0.125875        0.000791   
8        3.519791      0.041903         0.158801        0.001294   
9        1.900607      0.047803         0.102107        0.001770   
10       3.559790      0.017680         0.148930        0.001507   
11       5.690495      0.251873         0.220254        0.014325   
12       1.830361      0.054314         0.111464        0.022435   
13       3.491830      0.314309         0.142612        0.001700   
14       4.894746      0.014648         0.188766        0.002298   
15       1.750809      0.004907         0.099602        0.008191   
16       3.313226      0.005781         0.141278        0.001732   
17       4.910180      0.151459         0.182201        0.004455   
18       2.089178      0.010343         0.118913        0.002112   
19       4.028776      0.034710         0.189483        0.002211   
20       5.930317      0.056897         0.275332        0.031219   
21       2.050966      0.027681         0.119120        0.001450   
22       3.906237      0.015672         0.187776        0.001827   
23       5.783441      0.029964         0.253040        0.002939   
24       1.996059      0.013437         0.111711        0.001777   
25       3.799341      0.025596         0.173709        0.001641   
26       5.548325      0.057716         0.236878        0.002609   

   param_rfc__max_depth param_rfc__min_samples_split param_rfc__n_estimators  \
0                     5                            2                      50   
1                     5                            2                     100   
2                     5                            2                     150   
3                     5                           10                      50   
4                     5                           10                     100   
5                     5                           10                     150   
6                     5                           50                      50   
7                     5                           50                     100   
8                     5                           50                     150   
9                    10                            2                      50   
10                   10                            2                     100   
11                   10                            2                     150   
12                   10                           10                      50   
13                   10                           10                     100   
14                   10                           10                     150   
15                   10                           50                      50   
16                   10                           50                     100   
17                   10                           50                     150   
18                   15                            2                      50   
19                   15                            2                     100   
20                   15                            2                     150   
21                   15                           10                      50   
22                   15                           10                     100   
23                   15                           10                     150   
24                   15                           50                      50   
25                 

Based on our initial grid search results, we can infer that a larger max depth is needed to improve accuracy. 

In [77]:
# create our grid for the grid search parameters
params2 = {'rfc__n_estimators': [50, 100, 150],
           'rfc__max_depth': [15, 25, 50]}

# set up GridSearchCV object
grid_rfc2 = GridSearchCV(rfc_pipe, param_grid=params2, cv=5)

In [78]:
# fit our grid object with parameter updates for random forests to the training data
grid_rfc2.fit(X_train, y_train)

GridSearchCV(cv=5,
             estimator=Pipeline(steps=[('CT',
                                        ColumnTransformer(transformers=[('subpipe_num',
                                                                         Pipeline(steps=[('ss',
                                                                                          StandardScaler())]),
                                                                         [0, 2,
                                                                          17]),
                                                                        ('subpipe_cat',
                                                                         Pipeline(steps=[('ohe',
                                                                                          OneHotEncoder(handle_unknown='ignore',
                                                                                                        sparse=False))]),
                                            

In [79]:
grid_rfc2.best_params_

{'rfc__max_depth': 25, 'rfc__n_estimators': 150}

In [80]:
grid_rfc2.best_score_

0.7897721682958518

**From our second grid search, we attained an accuracy of 79.0% using a max_depth of 25 and an n_estimators of 150.**

In [81]:
pd.DataFrame(grid_rfc2.cv_results_)

mean_fit_time  std_fit_time  mean_score_time  std_score_time  \
0       2.114568      0.029804         0.123903        0.000802   
1       4.161690      0.146426         0.200091        0.009198   
2       5.921705      0.102354         0.264309        0.002643   
3       2.586275      0.016065         0.158190        0.001157   
4       5.010204      0.035641         0.262318        0.001268   
5       7.399083      0.053093         0.367357        0.003613   
6       2.818117      0.023917         0.171085        0.002885   
7       5.350099      0.065247         0.280799        0.002275   
8       7.946981      0.170325         0.397131        0.003374   

  param_rfc__max_depth param_rfc__n_estimators  \
0                   15                      50   
1                   15                     100   
2                   15                     150   
3                   25                      50   
4                   25                     100   
5                   25                     150   
6                   50                      50   
7                   50                     100   
8                   50                     150   

                                             params  split0_test_score  \
0   {'rfc__max_depth': 15, 'rfc__n_estimators': 50}           0.775833   
1  {'rfc__max_depth': 15, 'rfc__n_estimators': 100}           0.777866   
2  {'rfc__max_depth': 15, 'rfc__n_estimators': 150}           0.778543   
3   {'rfc__max_depth': 25, 'rfc__n_estimators': 50}           0.784980   
4  {'rfc__max_depth': 25, 'rfc__n_estimators': 100}           0.785658   
5  {'rfc__max_depth': 25, 'rfc__n_estimators': 150}           0.786110   
6   {'rfc__max_depth': 50, 'rfc__n_estimators': 50}           0.778656   
7  {'rfc__max_depth': 50, 'rfc__n_estimators': 100}           0.780350   
8  {'rfc__max_depth': 50, 'rfc__n_estimators': 150}           0.779447   

   split1_test_score  split2_test_score  split3_test_score  split4_test_score  \
0           0.783714           0.784504           0.786311           0.776711   
1           0.785747           0.785182           0.790490           0.777050   
2           0.785521           0.785521           0.788344           0.777276   
3           0.790038           0.788344           0.792862           0.783488   
4           0.791845           0.790603           0.793878           0.784504   
5           0.793314           0.791620           0.793991           0.783827   
6           0.780325           0.779083           0.782358           0.776485   
7           0.780099           0.778292           0.781229           0.775695   
8           0.780890           0.779309           0.781229           0.777615   

   mean_test_score  std_test_score  rank_test_score  
0         0.781415        0.004292                6  
1         0.783267        0.005095                4  
2         0.783041        0.004333                5  
3         0.787943        0.003388                3  
4         0.789298        0.003617                2  
5         0.789772        0.004063                1  
6         0.779382        0.001937                8  
7         0.779133        0.001967                9  
8         0.779698        0.001290                7

Based on our new grid search, we can see that a maximum depth greater than 15 but less than 50 is ideal. We will also try running the grid search with a higher number of trees in the random forest to improve accuracy.

In [82]:
# create our grid for the grid search parameters
params3 = {'rfc__n_estimators': [100, 150, 200],
           'rfc__max_depth': [20, 25, 30]}

# set up GridSearchCV object
grid_rfc3 = GridSearchCV(rfc_pipe, param_grid=params3, cv=5)

In [83]:
# Fit the grid object to our training data with updated grid params for n_estimators and max_depth
grid_rfc3.fit(X_train, y_train)

GridSearchCV(cv=5,
             estimator=Pipeline(steps=[('CT',
                                        ColumnTransformer(transformers=[('subpipe_num',
                                                                         Pipeline(steps=[('ss',
                                                                                          StandardScaler())]),
                                                                         [0, 2,
                                                                          17]),
                                                                        ('subpipe_cat',
                                                                         Pipeline(steps=[('ohe',
                                                                                          OneHotEncoder(handle_unknown='ignore',
                                                                                                        sparse=False))]),
                                            

In [84]:
grid_rfc3.best_params_

{'rfc__max_depth': 20, 'rfc__n_estimators': 150}

In [85]:
grid_rfc3.best_score_

0.7932732831246889

**From our third grid search, we attained an accuracy of 79.3% using a max_depth of 20 and an n_estimators of 150.** 

In [86]:
pd.DataFrame(grid_rfc3.cv_results_)

mean_fit_time  std_fit_time  mean_score_time  std_score_time  \
0       4.637129      0.021746         0.235885        0.003464   
1       6.845487      0.031213         0.327402        0.003434   
2       9.186073      0.218404         0.419098        0.001778   
3       5.312374      0.048106         0.264840        0.001764   
4       8.056202      0.240717         0.367862        0.001596   
5      10.270444      0.042270         0.467250        0.003328   
6       5.588438      0.067184         0.275694        0.002152   
7       8.295003      0.138406         0.387356        0.002912   
8      11.052190      0.047821         0.496877        0.002215   

  param_rfc__max_depth param_rfc__n_estimators  \
0                   20                     100   
1                   20                     150   
2                   20                     200   
3                   25                     100   
4                   25                     150   
5                   25                     200   
6                   30                     100   
7                   30                     150   
8                   30                     200   

                                             params  split0_test_score  \
0  {'rfc__max_depth': 20, 'rfc__n_estimators': 100}           0.789046   
1  {'rfc__max_depth': 20, 'rfc__n_estimators': 150}           0.791756   
2  {'rfc__max_depth': 20, 'rfc__n_estimators': 200}           0.792321   
3  {'rfc__max_depth': 25, 'rfc__n_estimators': 100}           0.785658   
4  {'rfc__max_depth': 25, 'rfc__n_estimators': 150}           0.786110   
5  {'rfc__max_depth': 25, 'rfc__n_estimators': 200}           0.785884   
6  {'rfc__max_depth': 30, 'rfc__n_estimators': 100}           0.780237   
7  {'rfc__max_depth': 30, 'rfc__n_estimators': 150}           0.783060   
8  {'rfc__max_depth': 30, 'rfc__n_estimators': 200}           0.781705   

   split1_test_score  split2_test_score  split3_test_score  split4_test_score  \
0           0.795686           0.796476           0.797267           0.786989   
1           0.795008           0.795121           0.797041           0.787441   
2           0.795686           0.794895           0.795686           0.787441   
3           0.791845           0.790603           0.793878           0.784504   
4           0.793314           0.791620           0.793991           0.783827   
5           0.794104           0.792410           0.794556           0.783601   
6           0.784504           0.784504           0.785408           0.778970   
7           0.785747           0.784956           0.785069           0.778292   
8           0.785747           0.785634           0.786085           0.779648   

   mean_test_score  std_test_score  rank_test_score  
0         0.793093        0.004224                3  
1         0.793273        0.003375                1  
2         0.793206        0.003136                2  
3         0.789298        0.003617                6  
4         0.789772        0.004063                5  
5         0.790111        0.004500                4  
6         0.782725        0.002601                9  
7         0.783425        0.002717                8  
8         0.783764        0.002608                7

In [87]:
# create our grid for the grid search parameters
params4 = {'rfc__n_estimators': [100, 150],
           'rfc__max_depth': [18, 20, 22],
           'rfc__max_features': ['auto', 'sqrt', 0.2]}

# set up GridSearchCV object
grid_rfc4 = GridSearchCV(rfc_pipe, param_grid=params4, cv=5)

In [88]:
grid_rfc4.fit(X_train, y_train)

GridSearchCV(cv=5,
             estimator=Pipeline(steps=[('CT',
                                        ColumnTransformer(transformers=[('subpipe_num',
                                                                         Pipeline(steps=[('ss',
                                                                                          StandardScaler())]),
                                                                         [0, 2,
                                                                          17]),
                                                                        ('subpipe_cat',
                                                                         Pipeline(steps=[('ohe',
                                                                                          OneHotEncoder(handle_unknown='ignore',
                                                                                                        sparse=False))]),
                                            

In [89]:
grid_rfc4.best_params_

{'rfc__max_depth': 20, 'rfc__max_features': 0.2, 'rfc__n_estimators': 150}

In [90]:
grid_rfc4.best_score_

0.7934991544239145

**From our fourth grid search, we attained an accuracy of 79.4% using a max_depth of 20, a max_features of 0.2, and an n_estimators of 150.** 

In [91]:
pd.DataFrame(grid_rfc4.cv_results_)

mean_fit_time  std_fit_time  mean_score_time  std_score_time  \
0        4.815963      0.184193         0.221336        0.001137   
1        6.920213      0.121069         0.307361        0.004218   
2        4.685156      0.045785         0.222388        0.001405   
3        6.872551      0.078340         0.306169        0.001072   
4        9.293461      0.024736         0.219723        0.000973   
5       13.792289      0.082229         0.302283        0.001929   
6        4.876834      0.050767         0.238045        0.003113   
7        7.288124      0.177262         0.328774        0.002695   
8        4.863515      0.021468         0.235150        0.002740   
9        7.325208      0.283075         0.328910        0.003899   
10       9.902877      0.205705         0.238224        0.006007   
11      14.505087      0.363425         0.323265        0.005085   
12       5.072541      0.034324         0.251659        0.001462   
13       7.488178      0.047145         0.345185        0.002459   
14       5.083127      0.032204         0.247249        0.001937   
15       7.637830      0.336011         0.349785        0.007471   
16      10.890408      0.442981         0.251591        0.005549   
17      15.136786      0.337962         0.337621        0.002603   

   param_rfc__max_depth param_rfc__max_features param_rfc__n_estimators  \
0                    18                    auto                     100   
1                    18                    auto                     150   
2                    18                    sqrt                     100   
3                    18                    sqrt                     150   
4                    18                     0.2                     100   
5                    18                     0.2                     150   
6                    20                    auto                     100   
7                    20                    auto                     150   
8                    20                    sqrt                     100   
9                    20                    sqrt                     150   
10                   20                     0.2                     100   
11                   20                     0.2                     150   
12                   22                    auto                     100   
13                   22                    auto                     150   
14                   22                    sqrt                     100   
15                   22                    sqrt                     150   
16                   22                     0.2                     100   
17                   22                     0.2                     150   

                                               params  split0_test_score  \
0   {'rfc__max_depth': 18, 'rfc__max_features': 'a...           0.788142   
1   {'rfc__max_depth': 18, 'rfc__max_features': 'a...           0.787126   
2   {'rfc__max_depth': 18, 'rfc__max_features': 's...           0.788142   
3   {'rfc__max_depth': 18, 'rfc__max_features': 's...           0.787126   
4   {'rfc__max_depth': 18, 'rfc__max_features': 0....           0.790966   
5   {'rfc__max_depth': 18, 'rfc__max_features': 0....           0.791417   
6   {'rfc__max_depth': 20, 'rfc__max_features': 'a...           0.789046   
7   {'rfc__max_depth': 20, 'rfc__max_features': 'a...           0.791756   
8   {'rfc__max_depth': 20, 'rfc__max_features': 's...           0.789046   
9   {'rfc__max_depth': 20, 'rfc__max_features': 's...           0.791756   
10  {'rfc__max_depth': 20, 'rfc__max_features': 0....           0.790514   
11  {'rfc__max_depth': 20, 'rfc__max_features': 0....           0.792434   
12  {'rfc__max_depth': 22, 'rfc__max_features': 'a...           0.788933   
13  {'rfc__max_depth': 22, 'rfc__max_features': 'a...           0.791078   
14  {'rfc__max_depth': 22, 'rfc__max_features': 's...           0.788933   
15  {'rfc__max_depth': 22, 'rfc__max_features': 's...           0.791

In [95]:
# create our massive grid for the grid search parameters
params5 = {'rfc__n_estimators': [125, 150, 175],
           'rfc__max_depth': [15, 20, 25],
           'rfc__max_features': ['sqrt', 0.1, 0.2, 0.5],
           'rfc__min_samples_leaf': [25, 50, 100],
           'rfc__min_impurity_decrease': [0, 0.025, 0.05, 0.075, 0.1],
           'rfc__criterion': ['gini', 'entropy', 'log_loss']}

# set up GridSearchCV object
grid_rfc5 = GridSearchCV(rfc_pipe, param_grid=params5, cv=5)

In [96]:
# Fit the grid search object to our training data to check numerous hyperparameters.
grid_rfc5.fit(X_train, y_train)

/Users/zacharypollatsek/opt/anaconda3/envs/learn-env/lib/python3.8/site-packages/sklearn/model_selection/_validation.py:548: FitFailedWarning: Estimator fit failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "/Users/zacharypollatsek/opt/anaconda3/envs/learn-env/lib/python3.8/site-packages/sklearn/model_selection/_validation.py", line 531, in _fit_and_score
    estimator.fit(X_train, y_train, **fit_params)
  File "/Users/zacharypollatsek/opt/anaconda3/envs/learn-env/lib/python3.8/site-packages/sklearn/pipeline.py", line 335, in fit
    self._final_estimator.fit(Xt, y, **fit_params_last_step)
  File "/Users/zacharypollatsek/opt/anaconda3/envs/learn-env/lib/python3.8/site-packages/sklearn/ensemble/_forest.py", line 386, in fit
    trees = Parallel(n_jobs=self.n_jobs, verbose=self.verbose,
  File "/Users/zacharypollatsek/opt/anaconda3/envs/learn-env/lib/python3.8/site-packages/joblib/parallel.py", line

/Users/zacharypollatsek/opt/anaconda3/envs/learn-env/lib/python3.8/site-packages/sklearn/model_selection/_validation.py:548: FitFailedWarning: Estimator fit failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "/Users/zacharypollatsek/opt/anaconda3/envs/learn-env/lib/python3.8/site-packages/sklearn/model_selection/_validation.py", line 531, in _fit_and_score
    estimator.fit(X_train, y_train, **fit_params)
  File "/Users/zacharypollatsek/opt/anaconda3/envs/learn-env/lib/python3.8/site-packages/sklearn/pipeline.py", line 335, in fit
    self._final_estimator.fit(Xt, y, **fit_params_last_step)
  File "/Users/zacharypollatsek/opt/anaconda3/envs/learn-env/lib/python3.8/site-packages/sklearn/ensemble/_forest.py", line 386, in fit
    trees = Parallel(n_jobs=self.n_jobs, verbose=self.verbose,
  File "/Users/zacharypollatsek/opt/anaconda3/envs/learn-env/lib/python3.8/site-packages/joblib/parallel.py", line

/Users/zacharypollatsek/opt/anaconda3/envs/learn-env/lib/python3.8/site-packages/sklearn/model_selection/_validation.py:548: FitFailedWarning: Estimator fit failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "/Users/zacharypollatsek/opt/anaconda3/envs/learn-env/lib/python3.8/site-packages/sklearn/model_selection/_validation.py", line 531, in _fit_and_score
    estimator.fit(X_train, y_train, **fit_params)
  File "/Users/zacharypollatsek/opt/anaconda3/envs/learn-env/lib/python3.8/site-packages/sklearn/pipeline.py", line 335, in fit
    self._final_estimator.fit(Xt, y, **fit_params_last_step)
  File "/Users/zacharypollatsek/opt/anaconda3/envs/learn-env/lib/python3.8/site-packages/sklearn/ensemble/_forest.py", line 386, in fit
    trees = Parallel(n_jobs=self.n_jobs, verbose=self.verbose,
  File "/Users/zacharypollatsek/opt/anaconda3/envs/learn-env/lib/python3.8/site-packages/joblib/parallel.py", line

/Users/zacharypollatsek/opt/anaconda3/envs/learn-env/lib/python3.8/site-packages/sklearn/model_selection/_validation.py:548: FitFailedWarning: Estimator fit failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "/Users/zacharypollatsek/opt/anaconda3/envs/learn-env/lib/python3.8/site-packages/sklearn/model_selection/_validation.py", line 531, in _fit_and_score
    estimator.fit(X_train, y_train, **fit_params)
  File "/Users/zacharypollatsek/opt/anaconda3/envs/learn-env/lib/python3.8/site-packages/sklearn/pipeline.py", line 335, in fit
    self._final_estimator.fit(Xt, y, **fit_params_last_step)
  File "/Users/zacharypollatsek/opt/anaconda3/envs/learn-env/lib/python3.8/site-packages/sklearn/ensemble/_forest.py", line 386, in fit
    trees = Parallel(n_jobs=self.n_jobs, verbose=self.verbose,
  File "/Users/zacharypollatsek/opt/anaconda3/envs/learn-env/lib/python3.8/site-packages/joblib/parallel.py", line

/Users/zacharypollatsek/opt/anaconda3/envs/learn-env/lib/python3.8/site-packages/sklearn/model_selection/_validation.py:548: FitFailedWarning: Estimator fit failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "/Users/zacharypollatsek/opt/anaconda3/envs/learn-env/lib/python3.8/site-packages/sklearn/model_selection/_validation.py", line 531, in _fit_and_score
    estimator.fit(X_train, y_train, **fit_params)
  File "/Users/zacharypollatsek/opt/anaconda3/envs/learn-env/lib/python3.8/site-packages/sklearn/pipeline.py", line 335, in fit
    self._final_estimator.fit(Xt, y, **fit_params_last_step)
  File "/Users/zacharypollatsek/opt/anaconda3/envs/learn-env/lib/python3.8/site-packages/sklearn/ensemble/_forest.py", line 386, in fit
    trees = Parallel(n_jobs=self.n_jobs, verbose=self.verbose,
  File "/Users/zacharypollatsek/opt/anaconda3/envs/learn-env/lib/python3.8/site-packages/joblib/parallel.py", line

...

/Users/zacharypollatsek/opt/anaconda3/envs/learn-env/lib/python3.8/site-packages/sklearn/model_selection/_validation.py:548: FitFailedWarning: Estimator fit failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "/Users/zacharypollatsek/opt/anaconda3/envs/learn-env/lib/python3.8/site-packages/sklearn/model_selection/_validation.py", line 531, in _fit_and_score
    estimator.fit(X_train, y_train, **fit_params)
  File "/Users/zacharypollatsek/opt/anaconda3/envs/learn-env/lib/python3.8/site-packages/sklearn/pipeline.py", line 335, in fit
    self._final_estimator.fit(Xt, y, **fit_params_last_step)
  File "/Users/zacharypollatsek/opt/anaconda3/envs/learn-env/lib/python3.8/site-packages/sklearn/ensemble/_forest.py", line 386, in fit
    trees = Parallel(n_jobs=self.n_jobs, verbose=self.verbose,
  File "/Users/zacharypollatsek/opt/anaconda3/envs/learn-env/lib/python3.8/site-packages/joblib/parallel.py", line

/Users/zacharypollatsek/opt/anaconda3/envs/learn-env/lib/python3.8/site-packages/sklearn/model_selection/_validation.py:548: FitFailedWarning: Estimator fit failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "/Users/zacharypollatsek/opt/anaconda3/envs/learn-env/lib/python3.8/site-packages/sklearn/model_selection/_validation.py", line 531, in _fit_and_score
    estimator.fit(X_train, y_train, **fit_params)
  File "/Users/zacharypollatsek/opt/anaconda3/envs/learn-env/lib/python3.8/site-packages/sklearn/pipeline.py", line 335, in fit
    self._final_estimator.fit(Xt, y, **fit_params_last_step)
  File "/Users/zacharypollatsek/opt/anaconda3/envs/learn-env/lib/python3.8/site-packages/sklearn/ensemble/_forest.py", line 386, in fit
    trees = Parallel(n_jobs=self.n_jobs, verbose=self.verbose,
  File "/Users/zacharypollatsek/opt/anaconda3/envs/learn-env/lib/python3.8/site-packages/joblib/parallel.py", line

/Users/zacharypollatsek/opt/anaconda3/envs/learn-env/lib/python3.8/site-packages/sklearn/model_selection/_validation.py:548: FitFailedWarning: Estimator fit failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "/Users/zacharypollatsek/opt/anaconda3/envs/learn-env/lib/python3.8/site-packages/sklearn/model_selection/_validation.py", line 531, in _fit_and_score
    estimator.fit(X_train, y_train, **fit_params)
  File "/Users/zacharypollatsek/opt/anaconda3/envs/learn-env/lib/python3.8/site-packages/sklearn/pipeline.py", line 335, in fit
    self._final_estimator.fit(Xt, y, **fit_params_last_step)
  File "/Users/zacharypollatsek/opt/anaconda3/envs/learn-env/lib/python3.8/site-packages/sklearn/ensemble/_forest.py", line 386, in fit
    trees = Parallel(n_jobs=self.n_jobs, verbose=self.verbose,
  File "/Users/zacharypollatsek/opt/anaconda3/envs/learn-env/lib/python3.8/site-packages/joblib/parallel.py", line

/Users/zacharypollatsek/opt/anaconda3/envs/learn-env/lib/python3.8/site-packages/sklearn/model_selection/_validation.py:548: FitFailedWarning: Estimator fit failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "/Users/zacharypollatsek/opt/anaconda3/envs/learn-env/lib/python3.8/site-packages/sklearn/model_selection/_validation.py", line 531, in _fit_and_score
    estimator.fit(X_train, y_train, **fit_params)
  File "/Users/zacharypollatsek/opt/anaconda3/envs/learn-env/lib/python3.8/site-packages/sklearn/pipeline.py", line 335, in fit
    self._final_estimator.fit(Xt, y, **fit_params_last_step)
  File "/Users/zacharypollatsek/opt/anaconda3/envs/learn-env/lib/python3.8/site-packages/sklearn/ensemble/_forest.py", line 386, in fit
    trees = Parallel(n_jobs=self.n_jobs, verbose=self.verbose,
  File "/Users/zacharypollatsek/opt/anaconda3/envs/learn-env/lib/python3.8/site-packages/joblib/parallel.py", line

GridSearchCV(cv=5,
             estimator=Pipeline(steps=[('CT',
                                        ColumnTransformer(transformers=[('subpipe_num',
                                                                         Pipeline(steps=[('ss',
                                                                                          StandardScaler())]),
                                                                         [0, 2,
                                                                          17]),
                                                                        ('subpipe_cat',
                                                                         Pipeline(steps=[('ohe',
                                                                                          OneHotEncoder(handle_unknown='ignore',
                                                                                                        sparse=False))]),
                                            

In [97]:
grid_rfc5.best_params_

{'rfc__criterion': 'entropy',
 'rfc__max_depth': 25,
 'rfc__max_features': 0.5,
 'rfc__min_impurity_decrease': 0,
 'rfc__min_samples_leaf': 25,
 'rfc__n_estimators': 175}

In [98]:
grid_rfc5.best_score_

0.7754286341819366

**From our fifth grid search, we attained an accuracy of 77.5% using a max_depth of 25, a max_features of 0.5, an entropy criterion, a minimum impurity decrease of 0, a minimum samples per leaf of 25, and an n_estimators of 175.** 

In [100]:
pd.DataFrame(grid_rfc5.cv_results_)

mean_fit_time  std_fit_time  mean_score_time  std_score_time  \
0          4.794858      0.487740         0.172364        0.011022   
1          5.422689      0.150138         0.208114        0.003024   
2          5.655950      0.117960         0.221955        0.003183   
3          3.900038      0.012762         0.166740        0.009165   
4          4.570771      0.091009         0.186371        0.002843   
...             ...           ...              ...             ...   
1615       0.246856      0.003851         0.000000        0.000000   
1616       0.255101      0.002922         0.000000        0.000000   
1617       0.240736      0.002747         0.000000        0.000000   
1618       0.247814      0.003270         0.000000        0.000000   
1619       0.255319      0.002941         0.000000        0.000000   

     param_rfc__criterion param_rfc__max_depth param_rfc__max_features  \
0                    gini                   15                    sqrt   
1                    gini                   15                    sqrt   
2                    gini                   15                    sqrt   
3                    gini                   15                    sqrt   
4                    gini                   15                    sqrt   
...                   ...                  ...                     ...   
1615             log_loss                   25                     0.5   
1616             log_loss                   25                     0.5   
1617             log_loss                   25                     0.5   
1618             log_loss                   25                     0.5   
1619             log_loss                   25                     0.5   

     param_rfc__min_impurity_decrease param_rfc__min_samples_leaf  \
0                                   0                          25   
1                                   0                          25   
2                                   0                          25   
3                                   0                          50   
4                                   0                          50   
...                               ...                         ...   
1615                              0.1                          50   
1616                              0.1                          50   
1617                              0.1                         100   
1618                              0.1                         100   
1619                              0.1                         100   

     param_rfc__n_estimators  \
0                        125   
1                        150   
2                        175   
3                        125   
4                        150   
...                      ...   
1615                     150   
1616                     175   
1617                     125   
1618                     150   
1619                     175   

                                                 params  split0_test_score  \
0     {'rfc__criterion': 'gini', 'rfc__max_depth': 1...           0.751101   
1     {'rfc__criterion': 'gini', 'rfc__max_depth': 1...           0.752343   
2     {'rfc__criterion': 'gini', 'rfc__max_depth': 1...           0.751214   
3     {'rfc__criterion': 'gini', 'rfc__max_depth': 1...           0.745793   
4     {'rfc__criterion': 'gini', 'rfc__max_depth': 1...           0.746471   
...                                                 ...                ...   
1615  {'rfc__criterion': 'log_loss', 'rfc__max_depth...                NaN   
1616  {'rfc__criterion': 'log_loss', 'rfc__max_depth...                NaN   
1617  {'rfc__criterion': 'log_loss', 'rfc__max_depth...                NaN   
1618  {'rfc__criterion': 'log_loss', 'rfc__max_depth...                NaN   
1619  {'rfc__criterion': 'log_loss', 'rfc__max_depth...                NaN   

      split1_test_score  split2_test_score  split3_test_score  \
0              0.754348           0.758188           0.76146

### XGBoost
